---
# Playground Series - S3E9: EDA

Autor: vsuguimoto

---

## Objetivo da análise
Essa é uma análise preliminar, iremos avaliar a qualidade dos dados e as relações entre as variáveis exógenas com a endógena.

## Sobre os dados

O dataset possui diversos fatores que afetam a força do concreto, como o material usado, tempo de secagem, etc.  

O desafio é predizer a força utilizando esses fatores como preditores.

**Descrição de cada coluna:**  
- CementComponent: o quanto de cimento foi misturado;
- BlastFurnaceSlag: o quanto de escória do alto forno foi misturado;
- FlyAshComponent: o quanto de cinzas foi misturado;
- WaterComponent: o quanto de água foi misturado;
- SuperplasticizerComponent: o quanto de aditivio superplastificante foi utilizado;
- CoarseAggregateComponent: o quanto de agregado grosso foi utilizado;
- FineAggregateComponent: o quanto de agregado fino foi utilizado;
- AgeInDays: tempo de secagem em dias;
- Strenght: força do concreto, variável alvo.

In [54]:
# Importação dos pacotes
# Pacotes de análise de dados
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns

from sklearn.model_selection import train_test_split
from ydata_profiling import ProfileReport

%matplotlib inline

# Desativa os alertas
import warnings
warnings.filterwarnings('ignore')

In [45]:
# Para evitar vazamento de dados e até mesmo para conseguirmos
# validar nosso modelo, é essencial realizar a separação de
# treino e teste

train, test = train_test_split(
    pd.read_csv('data/train.csv'),
    train_size=.7,
    random_state=42
)

In [46]:
PerfilDados = ProfileReport(
    train.iloc[:,1:], # Remove-se a coluna id do report
    title='Perfil dos dados'
)

In [47]:
PerfilDados.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**Key takeaways:**
- Há uma correlação linear forte entre o tempo de secagem e a força do concreto, ou seja, uma excelente variável preditora;
- Existem variáveis com um alto volume de zeros, pode não ser uma má ideia categorizá-las em grupo ou até mesmo em binários, são elas:
    - BlastFurnaceSlag;
    - FlyAshComponent;
    - SuperplasticizerComponent.
- Não existem valores nulos;
- Não existem valores duplicados.

**Informações úteis**

Baseado no comentário do [@jonbown](https://www.kaggle.com/competitions/playground-series-s3e9/discussion/391237):

> - Uma feature muito importante é a razão entre a WaterComponent e o CementComponent, quanto menor a razão, mais rápido o concreto seca e mais forte será no longo prazo;
> - Super plastificante é um aditivo custoso, é reservado apenas para quando o concreto necessita uma força acima do normal;
> - Agregado grosso são rochas largas que são adicionadas ao concreto, tipicamente aumentando a força;
> - Agregado fino são rochas pequenas que são adicionadas ao concreto, elas preenchem o que seria normalmente bolsas de ar, não influenciando na força do concreto, contudo quanto mais agregado fino, mais água será necessário;
> - Cinzas reduzem o quanto de água é necessário e permite o concreto ganhar força ao longo do tempo, reduzindo o custo inicial;
> - Escórias do alto forno, quanto mais maior a força de compressão aumenta com o passar do tempo;
> - Existem alguns estudos relacionados a razão entre cinzas e escórias, contudos não são conclusivos em relação ao ganho de força do concreto.

Dessa forma podemos criar diversas features para representar as relações ditas acima:

In [48]:
# Nota: será criado um arquivo .py para ser incorporado
# na pipeline de treinamento do modelo

def ft_water_cement_ratio(df):
    """Calcula a razão entre o componente de água e o componente de cimento

    Args:
        df (pd.DataFrame): Dataframe do desafio

    Returns:
        pd.DataFrame: Dataframe do desafio com a nova feature
    """

    df_copy = df[:]
    df_copy['WaterCementRatio'] = df_copy['WaterComponent']/df_copy['CementComponent']

    return df_copy

def ft_blastfurnaceslag_bin(df):
    """Categoriza a coluna BlastFurnaceSlag, verificando se ela é maior que zero

    Args:
        df (pd.DataFrame): Dataframe do desafio

    Returns:
        pd.DataFrame: Dataframe do desafio com a nova feature
    """

    df_copy = df[:]
    df_copy['BIN_BlastFurnaceSlag'] = [1 if x > 0 else 0 for x in df_copy['BlastFurnaceSlag']]

    return df_copy

def ft_flyash_bin(df):
    """Categoriza a coluna FlyAshComponent, verificando se ela é maior que zero

    Args:
        df (pd.DataFrame): Dataframe do desafio

    Returns:
        pd.DataFrame: Dataframe do desafio com a nova feature
    """

    df_copy = df[:]
    df_copy['BIN_FlyAshComponent'] = [1 if x > 0 else 0 for x in df_copy['FlyAshComponent']]

    return df_copy

def ft_superplasticizer_bin(df):
    """Categoriza a coluna SuperplasticizerComponent, verificando se ela é maior que zero

    Args:
        df (pd.DataFrame): Dataframe do desafio

    Returns:
        pd.DataFrame: Dataframe do desafio com a nova feature
    """

    df_copy = df[:]
    df_copy['BIN_SuperplasticizerComponent'] = [1 if x > 0 else 0 for x in df_copy['SuperplasticizerComponent']]

    return df_copy



In [49]:
# Feature engineering

train = ft_water_cement_ratio(train)
train = ft_blastfurnaceslag_bin(train)
train = ft_flyash_bin(train)
train = ft_superplasticizer_bin(train)

In [76]:
import statsmodels.api as sm

FEATURES = [
    'CementComponent','WaterComponent', 'CoarseAggregateComponent',
    'FineAggregateComponent', 'AgeInDays', 'WaterCementRatio',
    'BIN_BlastFurnaceSlag', 'BIN_FlyAshComponent', 'BIN_SuperplasticizerComponent'
]

TARGET = [
    'Strength'
]

X_train, y_train = train[FEATURES], train[TARGET]

X_train_sm = sm.add_constant(X_train)

In [78]:
ols = sm.OLS(y_train, X_train_sm)

ols.fit().summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Strength   R-squared:                       0.216
Model:                            OLS   Adj. R-squared:                  0.214
Method:                 Least Squares   F-statistic:                     115.3
Date:                Sat, 04 Mar 2023   Prob (F-statistic):          1.04e-191
Time:                        17:00:24   Log-Likelihood:                -15490.
No. Observations:                3784   AIC:                         3.100e+04
Df Residuals:                    3774   BIC:                         3.106e+04
Df Model:                           9                                         
Covariance Type:            nonrobust                                         
=================================================================================================
                                    coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------------------------
const                            37.8062      9.961      3.796      0.000      18.277      57.335
CementComponent                   0.0266      0.006      4.567      0.000       0.015       0.038
WaterComponent                   -0.0841      0.020     -4.301      0.000      -0.122      -0.046
CoarseAggregateComponent         -0.0015      0.004     -0.363      0.717      -0.010       0.007
FineAggregateComponent           -0.0032      0.004     -0.753      0.452      -0.012       0.005
AgeInDays                         0.0891      0.003     25.498      0.000       0.082       0.096
WaterCementRatio                  0.7828      2.022      0.387      0.699      -3.182       4.748
BIN_BlastFurnaceSlag              4.0192      0.641      6.269      0.000       2.762       5.276
BIN_FlyAshComponent              -1.9005      0.796     -2.389      0.017      -3.460      -0.341
BIN_SuperplasticizerComponent     7.3932      0.836      8.841      0.000       5.754       9.033
==============================================================================
Omnibus:                      131.875   Durbin-Watson:                   2.034
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              145.729
Skew:                           0.461   Prob(JB):                     2.27e-32
Kurtosis:                       3.273   Cond. No.                     5.53e+04
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 5.53e+04. This might indicate that there are
strong multicollinearity or other numerical problems.
"""